## Step 1: Create a Network

In [ ]:
!pip3 install bokeh

In [3]:
import networkx
from math import sqrt
from bokeh.models import ColumnDataSource
from bokeh.plotting import show, figure
from bokeh.io import output_notebook
from bokeh.models import HoverTool


In [4]:
network = networkx.read_gml('3.gml')
layout = networkx.spring_layout(network,
                                k=1.1/sqrt(network.number_of_nodes()),
                                iterations=100)

In [5]:
nodes, nodes_coordinates = zip(*sorted(layout.items()))
nodes_xs, nodes_ys = list(zip(*nodes_coordinates))
nodes_source = ColumnDataSource(dict(x=nodes_xs, y=nodes_ys,
                                     name=nodes))

## Step 2: Plot a Network

In [6]:
hover = HoverTool(tooltips=[('name', '@name'), ('id', '$index')])
plot = figure(plot_width=800, plot_height=400,
              tools=['tap', hover, 'box_zoom', 'reset'])
r_circles = plot.circle('x', 'y', source=nodes_source, size=10,
                        color='blue', level = 'overlay')

In [10]:
output_notebook(); show(plot)

Loading BokehJS ...

# Step 3: Add the edges

### Prepare the networkX edges

In [8]:
def get_edges_specs(_network, _layout):
    d = dict(xs=[], ys=[], alphas=[])
    weights = [d['weight'] for u, v, d in _network.edges(data=True)]
    max_weight = max(weights)
    calc_alpha = lambda h: 0.1 + 0.6 * (h / max_weight)

    # example: { ..., ('user47', 'da_bjoerni', {'weight': 3}), ... }
    for u, v, data in _network.edges(data=True):
        d['xs'].append([_layout[u][0], _layout[v][0]])
        d['ys'].append([_layout[u][1], _layout[v][1]])
        d['alphas'].append(calc_alpha(data['weight']))
    return d

In [11]:
lines_source = ColumnDataSource(get_edges_specs(network, layout))
r_lines = plot.multi_line('xs', 'ys', line_width=1.5,
                          alpha='alphas', color='navy',
                          source=lines_source)
show(plot)